In [1]:
#from textblob import TextBlob
#from langdetect.lang_detect_exception import LangDetectException
#from langdetect import detect

In [31]:
import pymongo
import json
from pymongo import MongoClient
from nltk.stem import WordNetLemmatizer
import re
import pandas as pd
import nltk
import nltk.stem
from nltk.corpus import stopwords
from nltk.corpus import sentiwordnet as swn
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer
import csv
import operator
from bson.objectid import ObjectId

In [3]:
client = MongoClient("176.31.43.33", 27017, maxPoolSize=50)
db = client['music']
db.authenticate('esieestudents', 'esiee2017projecte4qwant', mechanism = 'SCRAM-SHA-1', source='music')
collection=db['genius_collection']
cursor = collection.find()
list_of_dict = list()
for document in cursor:
    list_of_dict.append(document)

In [4]:
list_of_lyrics_en = []
list_of_lyrics_es = []
list_of_lyrics_fr = []

def store_lang(text_lang, liste, i):
    for x in range(i):
        if list_of_dict[x].get("lang") == text_lang:
            liste.append([str(list_of_dict[x]["_id"]),list_of_dict[x]["title"],list_of_dict[x]["lyrics"]]) 
            
store_lang("en",list_of_lyrics_en,len(list_of_dict))
store_lang("es",list_of_lyrics_es,1000)
store_lang("fr",list_of_lyrics_fr,len(list_of_dict))

In [5]:
len(list_of_lyrics_en)

627

In [6]:
list_of_lyrics_en_regex = []
list_of_lyrics_es_regex = []
list_of_lyrics_fr_regex = []

def regex_lyrics(list_dep,list_arriv):
    for ele in list_dep:
        liste=[ele[0]]
        for i in [1,2]:
            e=ele[i]
            e = re.sub(pattern="(\[.*?\])", repl= "", string=e)
            e = re.sub(pattern="\\n", repl= "", string=e)
            e = re.sub(pattern="\xa0", repl= "", string=e)
            e = re.sub("\(|\)", "", e)
            e = re.sub(",", "", e)
            e = re.sub("\'|\’", " ", e)
            e = re.sub("\"|\»|\«|\]|\[|\:|\#","", e)
            e = re.sub("\!|\?|\*", "", e)
            e = re.sub("[0-9]", "", e)
            e = re.sub("\s+", " ", e)
            liste.append(e)
        list_arriv.append(liste)
    return list_arriv

In [7]:
list_of_lyrics_en_regex = regex_lyrics(list_of_lyrics_en,list_of_lyrics_en_regex)
list_of_lyrics_es_regex = regex_lyrics(list_of_lyrics_es,list_of_lyrics_es_regex)
list_of_lyrics_fr_regex = regex_lyrics(list_of_lyrics_fr,list_of_lyrics_fr_regex)

In [8]:
def lowerword(liste):
    low = []
    for ele in liste:
        liste=[ele[0]]
        for i in [1,2]:
            e=ele[i]
            e = e.lower()
            liste.append(e)
        low.append(liste)
    return low

In [9]:
list_low_en = lowerword(list_of_lyrics_en_regex)
list_low_es = lowerword(list_of_lyrics_es_regex)
list_low_fr = lowerword(list_of_lyrics_fr_regex)

In [10]:
def lemmatiz(chaine):
    lemma = WordNetLemmatizer()
    lem = []
    lem2 = chaine.split(" ")
    for e in lem2:
        lem.append(lemma.lemmatize(e))
        
    return lem

In [11]:
#nltk.download()

In [13]:
stemmer_en=nltk.stem.SnowballStemmer('english')
stemmer_fr=nltk.stem.SnowballStemmer('french')
stemmer_fr=nltk.stem.SnowballStemmer('french')

In [14]:
def delete_stw(liste,liste_stw):
    for e in liste:
        if e in liste_stw:
            liste.remove(e)
    return liste

In [15]:
stw_en=stopwords.words('english')
stw_fr=stopwords.words('french')
stw_es=stopwords.words('spanish')
for letter in range(97,123):
    stw_fr.append(chr(letter))
    stw_en.append(chr(letter))
    #stw_es.append(chr(letter))

In [16]:
def stem_music_en(liste):
    return_list = []
    for e in liste:
        return_list.append(stemmer_en.stem(e))
    return return_list   

In [17]:
def stem_music(liste):
    return_list = []
    for e in liste:
        return_list.append(stemmer_fr.stem(e))
    return return_list   

In [19]:
#Dictionnaire français => sentiments : mots du champ lexical du sentiment
dict_sentiment_fr = {"joie" : "allégresse,bonheur,émotion,plaisir,liesse,enthousiasme,jubilation,satisfaction,gaieté,joyeux,euphorie,réjouissance,sérénité,félicité,ravissement,béatitude,exaltation,gaieté,jubiler,délice,foule,ineffable,rayonnant,volupté,humour,rire,sourire,transporté,alléluia,fête,vivre,bienveillance,compassion,goûter,délectation,euphorique,exultation,festin,hilarité,jouissance,joyeusement,réjouir,acclamation,aise,applaudissement,enfantine,exulter,maternité,bébé,enfant,paternité,rayonner,sauter,ami,entrain,religieux,vive,bénie,clameur,contenir,élan,émerveillement,emplit,gambader,heureux,paix,plénitude,réconfort,remplit,partage,célébration,réussite,paradis,épanouissement,illumine,liberté,amusement,dansant,danser,détente,distraction,divertissement,enjouement,fun,gai,jovialité,joyeuseté,jouer,férié,plaisanterie,ravi,buzz,synthés,caramelo,chante,sydney,voyage,frère,maman,papa,mère,père,soeur,fée,fêter,dream-team,heureux,optimiste,candide,positivité,positive,confiance,positive,attitude,avenir,insouciance,idéalisme,réalisme,bonheur,gaieté,intelligence,volonté,réalité,vitalité,progrès,sérénité,confiant,croire,dynamisme,inquiéter,persévérance,aise,béatitude,détente,euphorie,optimum,option,possible,soulagement,oubli,abstraction,relax,vouloir,espoir,pouvoir,réussite,paradis,possibilité,futur,avenir,innovation,idéal,confiant,enthousiaste,ambition".split(",") , 
                     "espoir" : "optimiste,candide,positivité,positive,confiance,positive,attitude,avenir,insouciance,idéalisme,réalisme,bonheur,gaieté,intelligence,volonté,réalité,vitalité,progrès,sérénité,confiant,croire,dynamisme,inquiéter,persévérance,aise,béatitude,détente,euphorie,optimum,option,possible,soulagement,oubli,abstraction,relax,vouloir,espoir,pouvoir,réussite,paradis,possibilité,futur,avenir,innovation,idéal,confiant,enthousiaste,ambition,espérance,déception,crainte,déçu,confiance,revoir,fol,vain,attente,libération,lueur,avenir,courage,meilleur,victoire,champion,désir,junior,ultime,redonner,souhait,retour,espérer,victoire,gagner,dernier,moment,remporter,résigné,réussite,salut,désillusion,fonde,illusion,inquiétudes,jeu,renaître,rêves,abandonner,foi,blessure,certitude,consolation,deuxième,jeune,mot,perspective,podium,sentiment,talent,but,confiance,en,soi,guérison,renoncer,résignation,saison,chimérique,décisive,sélectionné,vétéran,césar,chance,amoureux,caresser,conciliation,football,gardien,inébranlable,joueur,match,retrouver,sauver,temps,vie,gain,ressusciter,aspiration,assurance,consolant,conviction,croyance,délai,délivrance,flatteur,pause,prévision,prochain,projet,promesse,foi,espoir,charité,joie,attente,illusion,avenir,pandore,espérance,vie,miséricorde,promesse,fécondité,santé,confiance,vertu,salut,naissance,natalité,sportive,espérer,probabilité,chrétien,jésus,certitude,désir,gain,indicateur,dieu,éternelle,lueur,rêves,vaine,christ,progrès,au-delà,conviction,leurrer,présage,présomption,résultat,affliction,angoisses,ferveur,patients,résurrection,vivace,aspiration,consolation,survie,plénitude,anticipation,assurance,consolant,engagement,fiabilité,infantile,intuition,prévision,projet,sentiment,sûreté,voeu".split(","), 
                     "amour" : "amitié,cupidon,tendresse,passion,amour,sentiment,amoureux,baiser,affection,amant,aphrodite,éros,attachement,désir,haine,beauté,compassion,érotique,émotion,relation,jalousie,éternel,attirance,idylle,philtre,sexualité,aimer,bonheur,érotisme,plaisir,cœur,vénus,volupté,déesse,romantique,adoration,chant,filial,fraternel,luxure,romantisme,sincère,romance,conjugal,dévotion,dieu,paternel,charnel,fidélité,flamme,poème,épris,altruisme,âme,chagrin,lyrique,mariage,poésie,sentimental,sexuel,thème,séduction,sensualité,abnégation,chaste,chasteté,tendre,chanson,femme,mari,amourette,bien-aimé,couple,marivaux,narcissisme,feu,loyauté,passionné,romanesque,sacrifice,sonnet,charme,drame,enchantement,enfance,juliette,mélancolie,musset,passionnel,tourment,tragique,carquois,intimité,adonis,gloire,hélène,homosexuel,hétérosexuel,bisexuel,transgenre,idéal,jeunesse,ami,amor,étreinte,fille,follement,maternel,mère,maman,poète,tragédie,vénération,véritable,admiration,générosité,respect,tristan,déclaration,ferveur,infini,libertinage,nymphe,andromaque,beau,bien-aimée,délice,époux,garçon,prochain,récit,sincérité,virginité,affective,confidente,éprouver,adorable,ardeur,dévouement,extase,fidèle,infidélité,sensuel,consumer,fusionnel,idolâtrie,idyllique,roman,sœur,aphrodisiaque,inceste,ange,caresse,compagne,confidence,coquin,exprimer,foi,histoire,monsieur,sexe,adultère,amoureusement,enfant,fée,fiançailles,jaloux,partagé,bienfaisant,chéri,croire,instinctif,maternité,roméo,effusion,élan,enchanteur,exaltation,merveilleux,penchant,saint-valentin,unir,volage,amore,bébé,chérir,débordant,éperdument,hymen,lyrisme,passionnément,réciproque,tumultueux,vertu,vie,désir,passionné,sentiment,christ,tendresse,frénésie,délire,folie,enfance,fureur,geek,passionnel,penchant,épris,véritable,hobby,enthousiasme,émotion,goût,fougue,inclination,joie,exaltation,collectionneur,feu,romantique,vice,ambition,démesure,enflammer,mystère,passionnément,photographie,poésie,enthousiaste,flamme,sensuelle,égarement,béguin,esprit,ferveur,insatiable,loisir,nativité,relation,jardinage,attachement,chaleur,exalté,furie,jeunesse,voluptueux,ardente,cœur,déchaîner,dévotion,exaltant,femme,flatter,frénétique,inavouable,métier,naissante,satisfaire,consacrer,destructrice,inconscience,sublime,fanatisme,aimer,âme,appétit,brûlant,charnelle,consume,dévore,joueur,soudaine,vie,volupté,choral,équitation,conviction,emportement,envie,instinct,passe-temps,sentimental,talent,vive,collectionner,rêverie,fanatique,adoration,affection,affolement,agitation,débordement,élan,emballement,engouement,extase,fièvre,obstination".split(","), 
                     "peur" : "phobie,crainte,panique,frousse,angoisse,terreur,épouvante,trouille,horreur,anxiété,danger,trac,sentiment,claustrophobie,frayeur,cauchemar,haine,insécurité,dégoût,loup,culpabilité,épouvantail,claustrophobe,agoraphobie,tristesse,appréhension,folie,honte,irrationnelle,menace,phobique,pétoche,craintif,frisson,solitude,intimidation,araignée,trouble,situation,rumeur,chien,fantastique,effrayé,inquiétude,hanté,répulsion,monstre,paranoïa,sorcière,surmonter,hésitation,hallucination,flipper,cadavre,stress,sueur,violence,obscurité,rejet,saisissement,trembler,inconnu,hydrophobie,fantôme,enfer,alarme,chienne,couardise,stimulus,rassurer,russophobie,surnaturel,tremblant,tremble,timidité,arachnophobe,effraie,irraisonnée,peur,frémir,fuite,fuir,détresse,nomophobie,lâcheté,spectre,effroi,évitement,foutre,jetons,idée,arachnophobie,blocages,jetons,affolement,délinquant,chocottes,déplaire,contagion,cri,superstition,peureux,serpents,ogre,paralyse,palpite,horrifique,hurler,instinct,individu,halloween,frankenstein,foie,exprimer,effrayant,désespoir,agresseur,agression,acrophobie,anxieux,anuptaphobie,croque-mitaine,cacher,tomber,symptôme,souffrance,vision,voleur,warrior,zoophobie,politicien,réaction,refuser,néant,loup-garou,maléfique,méfiance,meurtre,représaille,provoquer,prudence,vertige,terroriser,timide,croyance,démon,attaquer,douleur,enfant,ennuyer,figer,castration,psychose,requin,jalousie,mourir,mysophobie,péril,répugnance,poltron,poltronnerie,préoccupation,pressentiment,tourment,thanatophobie,souci,veulerie,chantage,consternation,éraison,désarroi,autophobie,aquaphobie,ablutophobie,acarophobie,achluophobie,ailurophobie,affres,alerte,éreutophobie,exécration,égarement,emmerde,émoi,doute,détestation,hétérophobie,haptophobie,herpétophobie,frustration".split(","),
                     "tristesse" : "mélancolie,chagrin,deuil,désespoir,nostalgie,dégoût,souffrance,larme,triste,amertume,découragement,solitude,douleur,mélancolique,dépression,affliction,morne,lassitude,désolation,malheur,langueur,résignation,cafard,abattement,regret,pleurer,inquiétude,amer,compassion,consolation,rancoeur,spleen,acédie,profonde,ressentir,blues,glauque,adieu,déchirement,dépit,écoeurement,accablé,abattu,lamentation,morose,nuage,sombre,agacement,angoisse,bile,déception,déprime,envahit,éprouvé,anxiété,contrariété,fatigue,morosité,peine,tracas,monotonie,laideur,vie,allégresse,élégie,incurable,affection,affligé,déplaisir,dépressif,désespérance,douloureuse,écroulé,inconsolable,indéfinissable,mal,misanthropie,misère,pauvreté,paresse,isolement,mal-être,moral,rancune,accablement,attristé,bourdon,désœuvrement,drame,embarras,fiel,grisaille,hypocondrie,indicible,larmoyant,monotone,recueillement,saudade,souci,stupeur,tourment,tristounet,uniformité,suicide,pauvre,sdf,mort,cimetière,chialer,injustice,vieillesse,minable,piteux,pitié,pessimiste,pessimisme,volonté,défaitisme,mélancolie,scepticisme,mal,sinistrose,amer,morbide,morose,philosophique,résignation,subjectif,amertume,dégoût,fatalisme,hypocondrie,romantisme,symbolisme,conception,romantique,suicide,individualisme,dénouement,renoncement,négative,pensée,psychologique,vision,décadence,alarmisme,catastrophisme,incroyance,inquiétude,neurasthénie,nostalgie,souci,tracassin,tragique,misère,sdf,chômage,suicide,pauvre,cimetière,chialer,injustice,vieillesse,minable,piteux,pitié,pleur,trépas".split(","),
                     "colère" : "indignation,rage,irritation,colérique,ressentiment,fureur,haine,emportement,rancune,vengeance,furie,ire,courroux,frustration,orgueil,dépit,exaspération,furieux,énervement,révolte,attiser,inimitié,mépris,rancoeur,abattement,dégoût,irascibilité,juron,amertume,fâcher,bouffée,châtiment,impatience,menace,animosité,explosion,humiliation,violence,coléreux,déni,désespoir,violente,avarice,venger,jalousie,rogne,stupéfaction,grogne,agressivité,manifestant,aigreur,culpabilité,enfermer,injustice,irascible,châtier,courroucer,décolérer,encourir,excite,foudre,foudroyer,fulminant,irriter,maîtriser,merde,miséricordieux,rager,sourde,affront,agacement,bouillonner,crises,déchaînement,douleur,irritabilité,irritant,outré,refoulée,véhémence,acceptation,désarmer,déverse,déverser,expiation,hurler,impulsion,indigner,miséricorde,ressentir,sortie,terrible,hostilité,accepter,apprendre,avouer,bordel,coup,dédain,finir,fuir,insulté,mal,motard,nervosité,outrage,péché,capital,supplice,transformer,déceptions,déchaîner,ivre,malédiction,punir,tollé,tort,détourne,insolent,piquer,acharnement,acrimonie,antipathie,avidité,brûlure,colère,égarement,enflammé,éréthisme,fièvre,frémissant,frénésie,hargne,intempérance,intensité,interjection,malveillance,massue,menaçant,pétard,provoqué,putain,rancunière,tension,violent,agressivité,comportement,hargneux,menaçant,punk,agresser,combatif,haineux,méchant,provocateur,agressivement,attitude,hostiles,conquérant,hautain,insolent,intolérant,intrus,ton,passif,réputation,sarcastique,brutal,adversaire,mâle,tempérament,thérapie,pitbull,belliqueux,bruyant,piquant,devenait,mélodique,rock,accrocheur,acerbe,aguichant,aigre,bagarreur,batailleur,belligérant,castagneur,chicaneur,chicanier,coléreux,combattant,comminatoire,cruel,dangereux,déchaîner,défavorables,désobligeant,emporter,excitant,fielleux,furieux,grondant,guerrier,imminent,inamicaux,inquiétant,irascible,luttant,lutteur,malintentionné,malveillant,martial,offensif,peur,provocant,pugnace,querelleur,sanguinaire,séduisant,soldat,tapageur,tracassier,véhément,venimeux,vipérin".split(","),
                     "luxure" : "gourmandise,pute,bitch,orgueil,avarice,paresse,débauche,péché,stupre,amour,désir,pornographie,ivresse,cruauté,cupidité,sexe,luxurieux,luxure,vice,férocité,ivrognerie,libertinage,plaisir,dépravation,luxe,colère,extase,capital,envie,dollars,euros,argent,billet,sexualité,adultère,démon,excès,orgies,péchés,impureté,lubricité,sexuel,appétit,perverse,chasteté,enfer,libertin,richesse,volupté,lubrique,atrocité,bestialité,cul,dévergondage,enflammé,impudeur,indécence,inhumanité,luxuriance,luxuriant,obscénité,perversion,pudeur,sacrilège,sadisme,sauvagerie,scélérat,sensuel,viagra,raffinement,luxueux,richesse,hôtel,hôtellerie,ostentatoire,confort,goût,clientèle,joint,alcool,bijouterie,opulence,ostentation,joaillerie,parfum,magnificence,prostitution,profusion,somptuosité,denrée,palace,prestige,yacht,gastronomie,hôtelier,boutique,caviar,commodité,étalage,raffiné,vêtement,taxer,chic,prodigalité,volupté,berline,parure,superflu,cachemire,aisance,bijou,dentelle,dépense,ferrari,dubaï,apparat,contrefaçon,splendeur,résidences,automobile,bracelet,bling,parfumerie,prada,premium,clinquant,extravagant,fortune,milliardaire,orfèvrerie,paquebot,pompe,accessoires,mondain,nécessité,riche,villas,voitures,croisière,sensualité,bourge,brillant,casino,chambre,illicite,consommation,étalage,marque,oisiveté,opulent,pacha,paris,suite,fauchon,abus,aise,argenterie,débauche,démesure,luxuriance,convoitise,ambition,charnelle,envie,drogues,marijuana,cannabis,crack,putes,argent,billets,thune,fortune,liasse,jet".split(",")} 

In [20]:
#Dictionnaire anglais => sentiments : mots du champ lexical du sentiment
dict_sentiment_en = {"joie" : "joy,happiness,jubilation,cheerfulness,euphoria,rejoicing,serenity,bliss,joyfulness,exaltation,gaiety,joyful,delight,ineffable,radiant,voluptuousness,laugh,laughing,carried,hallelujah,kindness,delight,euphoric,exultation,feast,hilarity,enjoyment,cheer,joyous,applause,exult,maternity,baby,paternity,beaming,skip,buddy,friend,religious,blessed,clamor,hold,elan,wonder,filled,frolicking,happy,peace,fullness,comfort,fills,sharing,celebration,success,heaven,blooming,enlightenment,freedom,fun,dancing,relaxation,distraction,entertainment,playfulness,fun,joviality,joyfulness,play,holiday,joke,fun,laugh,buzz,synthesizer,sing,travel,brother,mom,mother,father,fairy,sister,team,football,clap".split(","), 
                     "espoir" : "forgive,pray,optimistic,candid,positivity,positive,confidence,positive attitude,future,recklessness,idealism,realism,happiness,joy,intelligence,will,reality,vitality,progress,calm,confident,believe,dynamic,caring,perseverance,comfortable,happiness,relaxation,euphoria,optimum,option,possible,relief,forgetfulness,abstraction,relax,want,hope,power,success,paradise,opportunity,future,future,innovation,perfect,confident,enthusiastic,ambition,confidence,goodbye,mad,vain,wait,release,glow,courage,best,victory,champ,desire,junior,ultimate,give,wish,return,win,last,time win,resigned,salvation,disillusionment,founded illusion concerns,game,reborn,dreams,faith,injury,certainty,comfort,second,young,short,perspective,podium,feeling,talent,purpose,confidence,in,self,healing,give,resignation,season,chimerical,decisive,selected,veteran,Caesar,luck,love,caress,conciliation,football,soccer,keeper,unwavering,player,game,find,save,time,life,winning,resurrect,aspiration,assurance,consolation,belief,creed,time,delivery,flattering,pause,forecast,next,project,promise,expectation,illusion,pandora,life,mercy,promise,fertility,health,virtue,salvation,birth,sports,probability,christian,jesus,certainty,desire,gain,flag,god,eternal,light,vain,christ,progress,belief,lure,omen,presumption,grief,enthusiasm,patient,consolation,fullness,insurance,consoling,commitment,reliability,infant,intuition,forecast,project,feeling,safety,wishes".split(","), 
                     "amour" : "cute,friendship,cupid,affection,passion,love,feelings,kiss,lover,aphrodite,eros,commitment,desire,hatred,beauty,compassion,erotic,emotion,relationship,jealousy,eternal,attraction,romance,love potion,sexuality,happiness,eroticism,pleasure,heart,venus,goddess,romantic,worship,singing,filial,fraternal,heartfelt,marriage,devotion,god,father,carnal,fidelity,flame,poem,altruism,soul,sorrow,lyrical,poetry,sentimental,sexual,theme,seduction,sensuality,self-denial,chaste,tender,song,wife,husband,love affair,narcissism,fire,loyalty,passion,sacrifice,sonnet,charm,drama,magic,childhood,juliet,melancholy,torment,quiver,privacy,adonis,helen,homosexual,heterosexual,bisexual,transgender,ideal,youth,friends,amor,hug,girl,madly,mother,mum,poet,tragedy,reverence,admiration,generosity,respect,tristan,statement,fervor,infinite,libertinism,nymph,andromaque,beautiful,beloved,husband,son,narrative,sincerity,virginity,emotional,confidante,experience,adorable,dedication,ecstasy,infidelity,sensual,consumer,fusion,idolatry,idyllic,romance,sister,aphrodisiac,incest,angel,caress,companion,confidence,naughty,express,history,sir,sex,adultery,lovingly,child,fairy,engagement,jealous,shared,beneficent,darling,believe, instinctive, maternity, romeo, shedding moose enchanting, exaltation, wonderful leaning valentine, unite, fickle, amore, baby, cherish, overflowing, madly, hymen, lyricism, passion, mutual, tumultuous, virtue, life, desire, passion, feeling, christ, tenderness, frenzy, delirium, madness, childhood, rage, geek, passion, addiction, love, true, hobbies, enthusiasm, emotion, taste, passion, inclination, joy, elation, collector, fire, romantic, vice, ambition, excess, fire, mystery, passion, photography, poetry, enthusiastic, flame, sensual, delusion, crush, spirit, enthusiasm, insatiable, leisure, nativity, relationship, gardening, dedication, warmth, exalted fury, youth, sensual, fiery, heart, wild, devotion, exhilarating, female, flatter, frantic, shameful, business, budding, meet, spend, destructive, unconsciousness, sublime, bigotry, love, soul, appetite, burning flesh, consume, devour, player, sudden, life, v olupté, choral, horse riding, conviction, passion, desire, instinct, hobby, sentimental, talented, bright, collect, daydreaming, fanatical adoration, affection, panic, agitation, overflow, momentum, excitement, enthusiasm, ecstasy, fever, obstinacy".split(","), 
                     "peur" : "skull,trouble,phobia,fear,panic,fright,terror,anxiety,trac,feeling,claustrophobia,nightmare,insecurity,disgust,wolf,guilt,scaremail,claustrophobic,agoraphobia,sadness,apprehension,madness,irrational,shame,threatening,fearful,shiver,thrill,loneliness,intimidation,spider,situation,rumor,dog,fantastic,frightened,anxiety,haunted,repulsion,monster,paranoia,witch,overcoming,hesitation,hallucination,corpse,stress,sweat,violence,darkness,rejection,seizure,trembling,unknown,hydrophobia,ghost,hell,alarm,bitch,cowardice,stimulus,reassurer,russophobia,supernatural,trembling,shyness,arachnophobe,fearless,irrational,quivering,leaking,flee,distress,nomophobia,dread,spectrum,fear,avoidance,tokens,idea,blockages,tokens,panic,delinquent,dislikes,contagion,scream,superstition,fearful,snake,ogre,paralyzes,palpate,horror,instinct,individual,halloween,frankenstein,liver,express,frightening,despair,aggression,acrophobia,anxious,anuptaphobia,hibiscus,killer,hiding,symptom,suffering,vision,thief,warrior,zoophobia,politician,reaction,refuse,deny,werewolf,evil,mistrust,murder,retaliate,provoke,caution,vertigo,terrorize,shy,belief,demon,attack,pain,child,boring,freezing,castration,psychosis,shark,jealousy,dying,mysophobia,peril,repugnance,cowardly,cowardice,preoccupation,foreboding,torment,thanatophobia,worry,vileness,blackmail,consternation,distrust,autophobia,aquaphobia,ablutophobia,acarophobia,achluophobia,aphorophobia,arrres,alertness,eruophobia,execration,misguidance,emotion,doubt,hatrophobia,haptophobia,herpetophobia,frustration".split(","),
                     "tristesse" : "trouble,melancholy,grief,mourning,despair,nostalgia,disgust,pain,tear,sad,bitterness,discouragement,loneliness,sadness,melancholy,depression,affliction,lassitude,desolation,misfortune,languor,resignation,cockroach,despondency,regret,crying,bitter,worry,compassion,consolation,rancor,spree,deep,acedia,feel,blues,glaucous,farewell,tearing,despite,disgust,overwhelmed,shot,lament,gloomy,cloud,aggression,anguish,boredom,disappointment,despair,disgruntled,displeasure,fatigue,frustration,gloomy,grief,loneliness,miserable,unhappiness,painful,despair,collapsed,inconsolable,indefinable,evil,misanthropy,misery,poverty,laziness,isolation,malaise,moral,rancor,despondency,sadness,boredom,dreadfulness,dreariness,embarrassment,festering,greed,hypochondria,unspeakable,dreary,monotonous,recollection,stunner,torment,uniformity,suicide,poor,homeless,cemetery,creeping,grievousness,grievous,old,age,shabby,pity,pessimistic,pessimism,will,defeatism,melancholy,skepticism,evil,bitter,morbid,philosophical,resignation,subjective,bitterness,disgust,fatalism,romanticism,symbolism,conception,romantic,suicide,individualism,denouement,renunciation,negative,thought,psychological,vision,decadence,alarmism,catastrophism,disbelief,disquiet,neurasthenia,nostalgia,worry,tracassin,tragic,misery,unemployment,suicide,poor,dead,death,cemetery,tears,injustice,old,age,shabby,pitiful,pity".split(","),
                     "colère" : "fck,fussing,cussing,nagging,skull,indignation,rage,irritation,choleric,resentment,fury,hate,anger,rancor,revenge,fury,ire,wrath,frustration,pride,despite,exasperation,furious,annoyance,revolt,fury,enmity,contempt,rancor,despondency,disgust,irascibility,expletive,bitterness,aggression,impatience,threat,animosity,explosion,humiliation,violence,anger,desperation,violent,avarice,avenge,jealousy,stumbles,amazement,growl,aggression,manifesting,sourness,guilt,lock,up,injustice,irascible,chastise,madness,dejure,incite,excite,thunder,thunder,fulminant,irritate,master,merciful,shit,deaf,rager,affront,annoyance,bubble,seizure,unleashing,irritability,irritant,outraged,repressed,vehement,acceptance,disarm,spill,pour,out,expiation,howl,impulse,indignation,mercy,exit,terrible,hostility,accept,learn,avenger,beating,dishonesty,end,disgrace,evil,fear,insulted,insulting,offense,overt,punish,outrage,sin,sting,greed,burning,anger,bewilderment,erupting,fever,quivering,frenzy,harassment,intemperance,intensity,interjection,malevolence,club,threatening,firecracker,provoked,whore,spiteful,tension,violent,aggression,behavior,snarling,threatening,punk,assault,combative,hateful,nasty,provocative,aggressively,attitude,hostile,conqueror,haughty,insolent,intolerant,intruder,tone,passive,reputation,sarcastic,brutal,adversary,male,temperament,therapy,pitbull,bellicose,noisy,nagging,became,melodic,rock,catchy,acerbic,eager,sour,brawler,battler,angry,belligerent,beatificer,quarrelsome,contentious,cruel,dangerous,dangerous,fight,fighter,flirting,frustrated,furious,irate,insecure,impetuous,irascible,malicious,martial,offending,offensive,provoking,pugnacious,raging,seductive,rascal,slayer,stubborn,venomous,viper,vicious,bitch,fuck,f*ck,niggas".split(","),
                     "luxure" : "motherfucking,motherfuck,vanity,pamela,gang,gangster,rack,vixen,pussy,homie,flashy,lamborghini,jewelry,rolex,gluttony,pride,greed,laziness,debauchery,sin,debauchery,love,lust,pornography, drunk, cruelty, greed, sex, luxury, lust, vice, ferocity, debauchery, pleasure, depravity, luxury, anger, ecstasy, capital, envy, dollars, euros, money, ticket, sexuality, adultery, demon, excess, orgies, sin, impurity, lust, sex, appetite, perverse, chastity, hell, libertine, wealth, lust, lustful, atrocity, bestiality,suck,rolex, ass, licentiousness, inflamed, immodesty, indecency, inhumanity, lush, lush, obscenity, perversion, decency, sacrilege, sadism, brutality, villain, sensual, viagra, refinement, luxury,naked,bomb-ass,dyke,tatoo, wealth, hotel, hotels, ostentatious, comfort, taste, customer, seal, alcohol, jewelery, opulent, ostentatious jewelry,weed, perfume, magnificence, prostitution, wealth, splendor, foodstuff, luxury hotel, luxury yacht gastronomy, hotel, shop, caviar, convenience, display, elegant, clothing, taxing, chic, prodigality, voluptuousness, sedan, adornment, superfluous, cashmere, ease, jewelry, lace, expense, ferrari, dubai, pageantry, counterfeiting, splendor, homes, automotive, bracelet, bling, perfume, prada, premium, flashy, extravagant, fortune, billionaire, silverware, liner, pump, accessories, fashionable, need rich, villas, cars, cruise, sensuality, bourge, bright, casino, room, wrongful use, display, brand, idleness, opulent, pasha, paris, subsequently fauchon, abuse, comfortable, silverware, debauchery, excess, lush, lust, ambition, sensual, envy, drugs, marijuana, cannabis, crack whores, money, cash, dosh, fortune, bundle, jet".split(",")} 

In [23]:
#Input: Dictionnaire de champ lexicaux à stemmatiser. 
#Output: Dictionnaire dict_sentiment_stem ou l'on a pris la racine des mots de dict_sentiment
def stem_lexical(dic):  
    dict_sentiment_stem = {"joie":"","espoir":"","amour":"","peur":"","tristesse":"","colère":"","luxure":""}
    for keys in dic:
        liste = []
        for values in dic[keys]:
            liste.append(stemmer_fr.stem(values))
        dict_sentiment_stem[keys] = set(liste)
    return dict_sentiment_stem

In [24]:
#Input: Dictionnaire de champ lexicaux à stemmatiser. 
#Output: Dictionnaire dict_sentiment_stem ou l'on a pris la racine des mots de dict_sentiment
def stem_lexical_en(dic):  
    dict_sentiment_stem = {"joie":"","espoir":"","amour":"","peur":"","tristesse":"","colère":"","luxure":""}
    for keys in dic:
        liste = []
        for values in dic[keys]:
            liste.append(stemmer_en.stem(values))
        dict_sentiment_stem[keys] = set(liste)
    return dict_sentiment_stem

In [25]:
dict_sentiment_fr_stem=stem_lexical(dict_sentiment_fr)
dict_sentiment_en_stem=stem_lexical_en(dict_sentiment_en)

In [26]:
print("Longueur des champs lexicaux français")
for k in dict_sentiment_fr_stem:
    print(k+": "+str(len(dict_sentiment_fr_stem[k])))

print("\nLongueur des champs lexicaux anglais")
for k in dict_sentiment_en_stem:
    print(k+": "+str(len(dict_sentiment_en_stem[k])))

Longueur des champs lexicaux français
joie: 131
espoir: 163
amour: 244
peur: 181
tristesse: 137
colère: 197
luxure: 158

Longueur des champs lexicaux anglais
joie: 72
espoir: 145
amour: 244
peur: 161
tristesse: 116
colère: 175
luxure: 156


In [29]:
#Input: musique à analyser et dictionnaire de sentiment
#Output: Dictionnaire => sentiment : nombre de mot dans la musique qui sont dans le champ lexical de ce sentiment
def count(music, dic_sent):
    dico = {"joie":0,"espoir":0,"amour":0,"peur":0,"tristesse":0,"colère":0,"luxure":0}
    for key in dico:
        for mot in music:
            if mot in dic_sent[key]:
                dico[key]+=1
    return dico

#Input: musique à prédire
#Output: résultat de count(musique stemmatisée,dic)
def predict_sentiment(music0, dic):
    a = lemmatiz(music0)
    list_fr = delete_stw(a,stw_fr)
    a = stem_music(a)
    return count(a,dic)

In [34]:
#Affiche une musique et le sentiment prédit
music_pred=list_low_fr[250][2]
print(music_pred)
senti=predict_sentiment(music_pred, dict_sentiment_fr_stem)
senti

IndexError: list index out of range

In [45]:
#Code test, prédit toutes les musiques dans list_low_en
#Output: Dictionnaire => sentiment : ids des musiques qui ont ce sentiment

dico_test = {"joie":[],"espoir":[],"amour":[],"peur":[],"tristesse":[],"colère":[],"luxure":[]}
for i in range(0,len(list_low_en)):
    music_pred_en=list_low_en[i][2]
    senti_en=predict_sentiment(music_pred_en, dict_sentiment_en_stem)
    dico_test[max(senti_en.items(), key=operator.itemgetter(1))[0]].append(i)
    
#Affiche pour chaque sentiment le nombre de musique qui ont ce sentiment
for k in dico_test:
    print(k+": "+str(len(dico_test[k])))

joie: 157
espoir: 1898
amour: 661
peur: 102
tristesse: 72
colère: 702
luxure: 100


In [27]:
i=333

In [33]:
#Affiche la musique n°1 et le sentiment associé
music_pred_en=list_low_en[i]
print(str(music_pred_en)+"\n")
senti_en=predict_sentiment(music_pred_en[2], dict_sentiment_en_stem)
print("Le sentiment dominant est: "+max(senti_en.items(), key=operator.itemgetter(1))[0])
print(senti_en)
print(i)
i+=10

['5a37f678e3bcfc4f49d49f3d', 'it s gangsta', 'it s g-a-n-g-s-t-a that s how it be and it s gon stay y all know whoooooooo that s how it be when you see me that s how it be in nyc y all know whoooooooo if it s me it s got to be if it s me it s got to be g-a-n-g-s-t-a y all know whoooooooo verse one i m still living la vida loca with wholesale prices on weed or coke-a for the hustlers for the customers trust the buzz it s have you makin one of the sounds that busta does woo hah they love me just because i m in the gallardo laughing like ricky ricardo ha ha ha ha with the -pounder pretty gangsta nigga i m the co-founder i know the difference between pimps and hoe-hounders i can tell when they ain t learn to lean they gold cups missing stones turning green i roll up wrist in chrome burning green like what s good hook verse two god was in a good mood on the day he made me i m from the projects it s the way it made me and i wouldn t change it for nothing i stay on point that s cuz i know the

In [69]:
#Rajoute le sentiment pour chaque musique anglaise à la base de donées
for i in range(0,len(list_low_en)):
    music_pred_en=list_low_en[i][2]
    senti_en=predict_sentiment(music_pred_en, dict_sentiment_en_stem)
    collection.update_one({'_id': ObjectId(list_low_en[i][0]) }, {"$set": {"sentiment": str(max(senti_en.items(), key=operator.itemgetter(1))[0])}}, upsert=False)
    print(list_low_en[i][0]+": "+max(senti_en.items(), key=operator.itemgetter(1))[0])

5a37f60de3bcfc4f49d4996b: espoir
5a37f60de3bcfc4f49d4996d: colère
5a37f60de3bcfc4f49d4996f: joie
5a37f60de3bcfc4f49d49971: amour
5a37f60de3bcfc4f49d49973: colère
5a37f60de3bcfc4f49d49977: espoir
5a37f60de3bcfc4f49d49979: espoir
5a37f60de3bcfc4f49d4997b: espoir
5a37f60de3bcfc4f49d49980: espoir
5a37f60ee3bcfc4f49d4998d: luxure
5a37f60ee3bcfc4f49d4998f: colère
5a37f60fe3bcfc4f49d49991: espoir
5a37f60fe3bcfc4f49d49993: espoir
5a37f60fe3bcfc4f49d49995: colère
5a37f60fe3bcfc4f49d49997: colère
5a37f60fe3bcfc4f49d49999: espoir
5a37f60fe3bcfc4f49d4999b: luxure
5a37f60fe3bcfc4f49d4999e: espoir
5a37f60fe3bcfc4f49d499a0: colère
5a37f610e3bcfc4f49d499a3: joie
5a37f610e3bcfc4f49d499a5: espoir
5a37f610e3bcfc4f49d499a7: espoir
5a37f610e3bcfc4f49d499a9: espoir
5a37f610e3bcfc4f49d499ab: colère
5a37f610e3bcfc4f49d499ad: colère
5a37f610e3bcfc4f49d499af: espoir
5a37f611e3bcfc4f49d499b3: colère
5a37f611e3bcfc4f49d499b5: espoir
5a37f611e3bcfc4f49d499b7: espoir
5a37f611e3bcfc4f49d499b9: espoir
5a37f611e3bcfc4

5a37f641e3bcfc4f49d49c67: amour
5a37f641e3bcfc4f49d49c69: espoir
5a37f641e3bcfc4f49d49c6b: espoir
5a37f642e3bcfc4f49d49c6f: espoir
5a37f642e3bcfc4f49d49c71: peur
5a37f642e3bcfc4f49d49c75: amour
5a37f642e3bcfc4f49d49c77: amour
5a37f642e3bcfc4f49d49c79: espoir
5a37f642e3bcfc4f49d49c7b: amour
5a37f642e3bcfc4f49d49c80: amour
5a37f642e3bcfc4f49d49c84: espoir
5a37f643e3bcfc4f49d49c88: espoir
5a37f643e3bcfc4f49d49c8a: peur
5a37f647e3bcfc4f49d49cc6: amour
5a37f648e3bcfc4f49d49ccc: espoir
5a37f648e3bcfc4f49d49cce: colère
5a37f649e3bcfc4f49d49cd0: colère
5a37f649e3bcfc4f49d49cd4: espoir
5a37f649e3bcfc4f49d49cd6: colère
5a37f649e3bcfc4f49d49cd8: peur
5a37f649e3bcfc4f49d49cda: colère
5a37f649e3bcfc4f49d49cdd: colère
5a37f64ae3bcfc4f49d49cdf: espoir
5a37f64ae3bcfc4f49d49ce1: amour
5a37f64ae3bcfc4f49d49ce3: espoir
5a37f64be3bcfc4f49d49ce5: espoir
5a37f64be3bcfc4f49d49ce7: colère
5a37f64be3bcfc4f49d49ce9: amour
5a37f64be3bcfc4f49d49ceb: amour
5a37f64be3bcfc4f49d49ced: colère
5a37f64be3bcfc4f49d49cf0:

5a37f695e3bcfc4f49d4a0bd: amour
5a37f696e3bcfc4f49d4a0bf: amour
5a37f696e3bcfc4f49d4a0c1: espoir
5a37f696e3bcfc4f49d4a0c3: amour
5a37f696e3bcfc4f49d4a0c6: espoir
5a37f696e3bcfc4f49d4a0c8: espoir
5a37f696e3bcfc4f49d4a0ca: espoir
5a37f697e3bcfc4f49d4a0cc: amour
5a37f697e3bcfc4f49d4a0ce: espoir
5a37f697e3bcfc4f49d4a0d2: amour
5a37f699e3bcfc4f49d4a0f0: espoir
5a37f6b6e3bcfc4f49d4a170: espoir
5a37f6bae3bcfc4f49d4a178: luxure
5a37f6bae3bcfc4f49d4a17a: colère
5a37f6bae3bcfc4f49d4a17c: peur
5a37f6bbe3bcfc4f49d4a181: espoir
5a37f6bbe3bcfc4f49d4a183: colère
5a37f6bbe3bcfc4f49d4a185: colère
5a37f6bbe3bcfc4f49d4a187: espoir
5a37f6bbe3bcfc4f49d4a189: colère
5a37f6bbe3bcfc4f49d4a18d: amour
5a37f6bbe3bcfc4f49d4a18f: espoir
5a37f6bbe3bcfc4f49d4a192: tristesse
5a37f6bbe3bcfc4f49d4a194: espoir
5a37f6bbe3bcfc4f49d4a196: espoir
5a37f6bbe3bcfc4f49d4a198: espoir
5a37f6bbe3bcfc4f49d4a19a: espoir
5a37f6bbe3bcfc4f49d4a19c: espoir
5a37f6bbe3bcfc4f49d4a19e: espoir
5a37f6bbe3bcfc4f49d4a1a0: amour
5a37f6bbe3bcfc4f

5a37f6dfe3bcfc4f49d4a398: espoir
5a37f6dfe3bcfc4f49d4a39a: amour
5a37f6e0e3bcfc4f49d4a39f: espoir
5a37f6e0e3bcfc4f49d4a3a1: espoir
5a37f6e0e3bcfc4f49d4a3a3: espoir
5a37f6e0e3bcfc4f49d4a3a5: amour
5a37f6e0e3bcfc4f49d4a3a7: espoir
5a37f6e1e3bcfc4f49d4a3a9: tristesse
5a37f6e1e3bcfc4f49d4a3ab: espoir
5a37f6e1e3bcfc4f49d4a3ad: espoir
5a37f6e1e3bcfc4f49d4a3af: tristesse
5a37f6e1e3bcfc4f49d4a3b1: amour
5a37f6e1e3bcfc4f49d4a3b3: amour
5a37f6e1e3bcfc4f49d4a3b5: amour
5a37f6e2e3bcfc4f49d4a3b7: espoir
5a37f6e2e3bcfc4f49d4a3ba: amour
5a37f6e2e3bcfc4f49d4a3bc: colère
5a37f6e2e3bcfc4f49d4a3be: joie
5a37f6e2e3bcfc4f49d4a3c0: joie
5a37f6e2e3bcfc4f49d4a3c2: espoir
5a37f6e2e3bcfc4f49d4a3c4: amour
5a37f6e3e3bcfc4f49d4a3c6: espoir
5a37f6e3e3bcfc4f49d4a3ca: espoir
5a37f6e3e3bcfc4f49d4a3cc: amour
5a37f6e3e3bcfc4f49d4a3ce: joie
5a37f6e4e3bcfc4f49d4a3d0: amour
5a37f6e4e3bcfc4f49d4a3d4: colère
5a37f6e4e3bcfc4f49d4a3d8: colère
5a37f6e4e3bcfc4f49d4a3da: colère
5a37f6e5e3bcfc4f49d4a3dc: amour
5a37f6e5e3bcfc4f49d4

5a37f721e3bcfc4f49d4a753: espoir
5a37f722e3bcfc4f49d4a755: joie
5a37f722e3bcfc4f49d4a757: espoir
5a37f722e3bcfc4f49d4a759: espoir
5a37f722e3bcfc4f49d4a75b: espoir
5a37f722e3bcfc4f49d4a75d: amour
5a37f722e3bcfc4f49d4a75f: espoir
5a37f722e3bcfc4f49d4a761: joie
5a37f723e3bcfc4f49d4a764: espoir
5a37f723e3bcfc4f49d4a766: amour
5a37f723e3bcfc4f49d4a76a: peur
5a37f723e3bcfc4f49d4a76c: espoir
5a37f723e3bcfc4f49d4a76e: espoir
5a37f724e3bcfc4f49d4a772: espoir
5a37f724e3bcfc4f49d4a774: espoir
5a37f724e3bcfc4f49d4a776: espoir
5a37f724e3bcfc4f49d4a77a: amour
5a37f724e3bcfc4f49d4a77c: joie
5a37f724e3bcfc4f49d4a77e: espoir
5a37f724e3bcfc4f49d4a780: espoir
5a37f725e3bcfc4f49d4a782: espoir
5a37f725e3bcfc4f49d4a786: espoir
5a37f725e3bcfc4f49d4a78a: espoir
5a37f725e3bcfc4f49d4a78c: espoir
5a37f725e3bcfc4f49d4a78e: espoir
5a37f726e3bcfc4f49d4a790: amour
5a37f726e3bcfc4f49d4a792: amour
5a37f726e3bcfc4f49d4a794: espoir
5a37f726e3bcfc4f49d4a796: amour
5a37f726e3bcfc4f49d4a798: espoir
5a37f726e3bcfc4f49d4a79b

...

5a3851d6e3bcfc4f49d82f4e: colère
5a3851d6e3bcfc4f49d82f50: espoir
5a3851d6e3bcfc4f49d82f52: colère
5a3851d6e3bcfc4f49d82f54: espoir
5a3851d6e3bcfc4f49d82f56: colère
5a3851d6e3bcfc4f49d82f58: colère
5a3851d6e3bcfc4f49d82f5a: colère
5a3851d7e3bcfc4f49d82f5c: colère
5a3851d7e3bcfc4f49d82f5e: espoir
5a3851d7e3bcfc4f49d82f60: colère
5a3851d7e3bcfc4f49d82f64: colère
5a3851d7e3bcfc4f49d82f66: colère
5a3851d8e3bcfc4f49d82f68: espoir
5a3851d8e3bcfc4f49d82f6a: colère
5a3851d8e3bcfc4f49d82f6c: amour
5a3851d8e3bcfc4f49d82f6f: colère
5a3851d8e3bcfc4f49d82f71: colère
5a3851d8e3bcfc4f49d82f73: espoir
5a3851d8e3bcfc4f49d82f75: amour
5a3851d9e3bcfc4f49d82f77: colère
5a3851d9e3bcfc4f49d82f79: espoir
5a3851d9e3bcfc4f49d82f7d: colère
5a3851d9e3bcfc4f49d82f7f: espoir
5a3851d9e3bcfc4f49d82f81: espoir
5a3851d9e3bcfc4f49d82f83: espoir
5a3851d9e3bcfc4f49d82f85: colère
5a3851dae3bcfc4f49d82f87: espoir
5a3851dae3bcfc4f49d82f89: colère
5a3851dae3bcfc4f49d82f8b: espoir
5a3851dae3bcfc4f49d82f8d: luxure
5a3851dae3bc

5a385203e3bcfc4f49d831c9: espoir
5a385203e3bcfc4f49d831cb: espoir
5a385203e3bcfc4f49d831cd: colère
5a385203e3bcfc4f49d831cf: colère
5a385203e3bcfc4f49d831d1: espoir
5a385203e3bcfc4f49d831d3: colère
5a385203e3bcfc4f49d831d5: espoir
5a385203e3bcfc4f49d831d7: colère
5a385203e3bcfc4f49d831d9: colère
5a385204e3bcfc4f49d831dd: espoir
5a385204e3bcfc4f49d831df: espoir
5a385204e3bcfc4f49d831e1: colère
5a385204e3bcfc4f49d831e3: espoir
5a385204e3bcfc4f49d831e5: colère
5a385205e3bcfc4f49d831e7: espoir
5a385205e3bcfc4f49d831e9: colère
5a385205e3bcfc4f49d831eb: colère
5a385205e3bcfc4f49d831ed: luxure
5a385205e3bcfc4f49d831ef: colère
5a385205e3bcfc4f49d831f1: luxure
5a385205e3bcfc4f49d831f3: colère
5a385205e3bcfc4f49d831f5: espoir
5a385205e3bcfc4f49d831f7: espoir
5a385206e3bcfc4f49d831f9: tristesse
5a385206e3bcfc4f49d831fb: espoir
5a385206e3bcfc4f49d831fd: espoir
5a385206e3bcfc4f49d831ff: amour
5a385206e3bcfc4f49d83203: colère
5a385207e3bcfc4f49d83205: colère
5a385207e3bcfc4f49d83207: luxure
5a385207

5a38523ce3bcfc4f49d834f1: amour
5a38523de3bcfc4f49d834f5: amour
5a38523de3bcfc4f49d834f9: amour
5a38523de3bcfc4f49d834fb: tristesse
5a38523de3bcfc4f49d834ff: colère
5a38523ee3bcfc4f49d83505: colère
5a38523ee3bcfc4f49d83507: colère
5a38523ee3bcfc4f49d83509: colère
5a38523ee3bcfc4f49d8350b: colère
5a38523ee3bcfc4f49d8350d: colère
5a38523ee3bcfc4f49d8350f: peur
5a38523ee3bcfc4f49d83511: peur
5a38523ee3bcfc4f49d83515: colère
5a38523fe3bcfc4f49d83517: espoir
5a38523fe3bcfc4f49d83519: colère
5a38523fe3bcfc4f49d8351b: colère
5a38523fe3bcfc4f49d8351d: espoir
5a38523fe3bcfc4f49d8351f: colère
5a38523fe3bcfc4f49d83521: luxure
5a38523fe3bcfc4f49d83525: colère
5a385240e3bcfc4f49d83527: colère
5a385240e3bcfc4f49d83529: espoir
5a385240e3bcfc4f49d8352b: colère
5a385240e3bcfc4f49d8352d: espoir
5a385240e3bcfc4f49d8352f: espoir
5a385240e3bcfc4f49d83531: espoir
5a385240e3bcfc4f49d83533: espoir
5a385240e3bcfc4f49d83535: espoir
5a385240e3bcfc4f49d83537: espoir
5a385241e3bcfc4f49d83539: colère
5a385241e3bcfc

5a385262e3bcfc4f49d8372c: colère
5a385262e3bcfc4f49d8372e: espoir
5a385262e3bcfc4f49d83730: amour
5a385262e3bcfc4f49d83732: espoir
5a385262e3bcfc4f49d83734: espoir
5a385262e3bcfc4f49d83736: espoir
5a385263e3bcfc4f49d83738: luxure
5a385263e3bcfc4f49d8373a: espoir
5a385263e3bcfc4f49d8373c: espoir
5a385263e3bcfc4f49d8373e: espoir
5a385263e3bcfc4f49d83740: espoir
5a385263e3bcfc4f49d83742: amour
5a385263e3bcfc4f49d83744: amour
5a385264e3bcfc4f49d83746: amour
5a385264e3bcfc4f49d83748: espoir
5a385264e3bcfc4f49d8374a: amour
5a385264e3bcfc4f49d8374c: peur
5a385264e3bcfc4f49d8374e: joie
5a385264e3bcfc4f49d83751: tristesse
5a385265e3bcfc4f49d83753: luxure
5a385265e3bcfc4f49d83759: espoir
5a38526ce3bcfc4f49d837ad: colère
5a38526ce3bcfc4f49d837af: colère
5a38526de3bcfc4f49d837b3: espoir
5a38526de3bcfc4f49d837b5: joie
5a38526de3bcfc4f49d837b7: amour
5a38526de3bcfc4f49d837b9: joie
5a38526de3bcfc4f49d837bb: amour
5a38526de3bcfc4f49d837bd: amour
5a38526de3bcfc4f49d837bf: espoir
5a38526de3bcfc4f49d837c

5a3852aee3bcfc4f49d83a58: colère
5a3852aee3bcfc4f49d83a5a: colère
5a3852aee3bcfc4f49d83a5c: espoir
5a3852aee3bcfc4f49d83a5e: espoir
5a3852aee3bcfc4f49d83a60: colère
5a3852afe3bcfc4f49d83a62: espoir
5a3852afe3bcfc4f49d83a64: colère
5a3852afe3bcfc4f49d83a66: luxure
5a3852afe3bcfc4f49d83a68: espoir
5a3852afe3bcfc4f49d83a6a: colère
5a3852afe3bcfc4f49d83a6c: tristesse
5a3852b0e3bcfc4f49d83a6e: colère
5a3852b0e3bcfc4f49d83a70: colère
5a3852b0e3bcfc4f49d83a72: colère
5a3852b0e3bcfc4f49d83a74: colère
5a3852b0e3bcfc4f49d83a76: colère
5a3852b0e3bcfc4f49d83a78: colère
5a3852b0e3bcfc4f49d83a7a: colère
5a3852b0e3bcfc4f49d83a7c: espoir
5a3852b1e3bcfc4f49d83a7e: colère
5a3852b1e3bcfc4f49d83a80: colère
5a3852b1e3bcfc4f49d83a82: amour
5a3852b1e3bcfc4f49d83a84: colère
5a3852b1e3bcfc4f49d83a88: espoir
5a3852b1e3bcfc4f49d83a8a: colère
5a3852b1e3bcfc4f49d83a8c: colère
5a3852b1e3bcfc4f49d83a8e: colère
5a3852b2e3bcfc4f49d83a90: espoir
5a3852b2e3bcfc4f49d83a92: peur
5a3852b2e3bcfc4f49d83a94: colère
5a3852b2e3

In [68]:
#Rajoute le sentiment pour chaque musique française à la base de donées
for i in range(0,len(list_low_fr)):
    music_pred_fr=list_low_fr[i][2]
    senti_fr=predict_sentiment(music_pred_fr)

    collection.update_one({'_id': ObjectId(list_low_fr[i][0]) }, {"$set": {"sentiment": str(max(senti_fr.items(), key=operator.itemgetter(1))[0])}}, upsert=False)
    print(list_low_fr[i][0]+": "+max(senti_fr.items(), key=operator.itemgetter(1))[0])

5a37f642e3bcfc4f49d49c7e: luxure
5a37f642e3bcfc4f49d49c82: tristesse
5a37f643e3bcfc4f49d49c86: amour
5a37f643e3bcfc4f49d49c8c: amour
5a37f644e3bcfc4f49d49c8f: luxure
5a37f644e3bcfc4f49d49c91: amour
5a37f644e3bcfc4f49d49c93: amour
5a37f644e3bcfc4f49d49c95: espoir
5a37f644e3bcfc4f49d49c97: amour
5a37f644e3bcfc4f49d49c99: tristesse
5a37f644e3bcfc4f49d49c9b: amour
5a37f645e3bcfc4f49d49c9f: joie
5a37f645e3bcfc4f49d49ca1: luxure
5a37f645e3bcfc4f49d49ca3: luxure
5a37f645e3bcfc4f49d49ca5: luxure
5a37f645e3bcfc4f49d49ca9: colère
5a37f646e3bcfc4f49d49cac: espoir
5a37f646e3bcfc4f49d49cae: joie
5a37f646e3bcfc4f49d49cb0: espoir
5a37f646e3bcfc4f49d49cb2: amour
5a37f646e3bcfc4f49d49cb4: peur
5a37f647e3bcfc4f49d49cb6: tristesse
5a37f647e3bcfc4f49d49cb8: amour
5a37f647e3bcfc4f49d49cbb: espoir
5a37f647e3bcfc4f49d49cbd: luxure
5a37f647e3bcfc4f49d49cc0: espoir
5a37f647e3bcfc4f49d49cc2: amour
5a37f647e3bcfc4f49d49cc4: espoir
5a37f648e3bcfc4f49d49cc8: amour
5a37f648e3bcfc4f49d49cca: espoir
5a37f649e3bcfc4f4

5a37f96ae3bcfc4f49d4c188: amour
5a37f96ae3bcfc4f49d4c18a: espoir
5a37f96ae3bcfc4f49d4c18c: amour
5a37f96ae3bcfc4f49d4c18e: espoir
5a37f96ae3bcfc4f49d4c192: espoir
5a37f96be3bcfc4f49d4c194: amour
5a37f96be3bcfc4f49d4c196: espoir
5a37f96be3bcfc4f49d4c198: joie
5a37f96be3bcfc4f49d4c19a: peur
5a37f96be3bcfc4f49d4c19c: luxure
5a37f96ce3bcfc4f49d4c1a7: fierté
5a37f96ce3bcfc4f49d4c1a9: espoir
5a37f96ce3bcfc4f49d4c1ad: colère
5a37f96de3bcfc4f49d4c1b1: espoir
5a37f96de3bcfc4f49d4c1b3: joie
5a37f96de3bcfc4f49d4c1b5: peur
5a37f96de3bcfc4f49d4c1b7: espoir
5a37f96de3bcfc4f49d4c1b9: espoir
5a37f96de3bcfc4f49d4c1bb: amour
5a37f96de3bcfc4f49d4c1bd: espoir
5a37f96ee3bcfc4f49d4c1c0: espoir
5a37f96ee3bcfc4f49d4c1c2: joie
5a37f96ee3bcfc4f49d4c1c4: colère
5a37f96fe3bcfc4f49d4c1c7: peur
5a37f96fe3bcfc4f49d4c1c9: espoir
5a37f96fe3bcfc4f49d4c1cb: espoir
5a37f96fe3bcfc4f49d4c1cd: amour
5a37f96fe3bcfc4f49d4c1cf: espoir
5a37f96fe3bcfc4f49d4c1d1: amour
5a37f96fe3bcfc4f49d4c1d3: peur
5a37f970e3bcfc4f49d4c1d5: amou

5a37fe3ee3bcfc4f49d4eb02: peur
5a37fe3fe3bcfc4f49d4eb05: joie
5a37fe3fe3bcfc4f49d4eb09: colère
5a37fe3fe3bcfc4f49d4eb0b: luxure
5a37fe3fe3bcfc4f49d4eb0d: joie
5a37fe3fe3bcfc4f49d4eb0f: espoir
5a37fe3fe3bcfc4f49d4eb11: espoir
5a37fe40e3bcfc4f49d4eb13: colère
5a37fe40e3bcfc4f49d4eb15: amour
5a37fe40e3bcfc4f49d4eb17: amour
5a37fe40e3bcfc4f49d4eb19: espoir
5a37fe40e3bcfc4f49d4eb1b: peur
5a37fe41e3bcfc4f49d4eb1d: amour
5a37fe41e3bcfc4f49d4eb21: tristesse
5a37fe41e3bcfc4f49d4eb25: espoir
5a37fe41e3bcfc4f49d4eb27: colère
5a37fe41e3bcfc4f49d4eb29: peur
5a37fe41e3bcfc4f49d4eb2b: espoir
5a37fe42e3bcfc4f49d4eb2d: espoir
5a37fe42e3bcfc4f49d4eb2f: amour
5a37fe42e3bcfc4f49d4eb31: espoir
5a37fe42e3bcfc4f49d4eb33: amour
5a37fe43e3bcfc4f49d4eb35: amour
5a37fe43e3bcfc4f49d4eb37: espoir
5a37fe43e3bcfc4f49d4eb39: luxure
5a37fe43e3bcfc4f49d4eb3b: amour
5a37fe43e3bcfc4f49d4eb3d: amour
5a37fe43e3bcfc4f49d4eb3f: amour
5a37fe44e3bcfc4f49d4eb41: espoir
5a37fe44e3bcfc4f49d4eb43: luxure
5a37fe44e3bcfc4f49d4eb47: 

5a380834e3bcfc4f49d54b55: espoir
5a380834e3bcfc4f49d54b57: espoir
5a380834e3bcfc4f49d54b59: amour
5a380834e3bcfc4f49d54b5d: tristesse
5a380835e3bcfc4f49d54b63: espoir
5a380835e3bcfc4f49d54b65: joie
5a380835e3bcfc4f49d54b6f: joie
5a380862e3bcfc4f49d54db4: joie
5a380862e3bcfc4f49d54db6: espoir
5a380863e3bcfc4f49d54db8: espoir
5a380863e3bcfc4f49d54dba: colère
5a380863e3bcfc4f49d54dbc: peur
5a380863e3bcfc4f49d54dbe: tristesse
5a380863e3bcfc4f49d54dc0: joie
5a380864e3bcfc4f49d54dc2: amour
5a380864e3bcfc4f49d54dc4: espoir
5a380864e3bcfc4f49d54dc6: espoir
5a380864e3bcfc4f49d54dc8: peur
5a380864e3bcfc4f49d54dca: espoir
5a380865e3bcfc4f49d54dd2: tristesse
5a380872e3bcfc4f49d54e7b: joie
5a38088ce3bcfc4f49d54fce: amour
5a38088de3bcfc4f49d54fd6: amour
5a38088ee3bcfc4f49d54fda: peur
5a38088ee3bcfc4f49d54fdc: luxure
5a38088ee3bcfc4f49d54fde: amour
5a38088ee3bcfc4f49d54fe0: amour
5a38088fe3bcfc4f49d54fe4: amour
5a38088fe3bcfc4f49d54fe6: colère
5a38088fe3bcfc4f49d54fea: joie
5a38088fe3bcfc4f49d54fec: 

5a380af1e3bcfc4f49d563e6: amour
5a380af1e3bcfc4f49d563e8: amour
5a380af1e3bcfc4f49d563ea: amour
5a380af1e3bcfc4f49d563ec: amour
5a380af1e3bcfc4f49d563ee: amour
5a380af2e3bcfc4f49d563f0: colère
5a380af2e3bcfc4f49d563f4: amour
5a380af2e3bcfc4f49d563f8: espoir
5a380af3e3bcfc4f49d563fa: amour
5a380af3e3bcfc4f49d563fc: luxure
5a380af3e3bcfc4f49d563fe: tristesse
5a380af4e3bcfc4f49d56400: amour
5a380af4e3bcfc4f49d56402: amour
5a380af4e3bcfc4f49d56404: amour
5a380af4e3bcfc4f49d56406: amour
5a380af4e3bcfc4f49d56408: amour
5a380af5e3bcfc4f49d5640a: amour
5a380af5e3bcfc4f49d5640d: colère
5a380af5e3bcfc4f49d5640f: amour
5a380af5e3bcfc4f49d56411: colère
5a380af6e3bcfc4f49d56415: amour
5a380af6e3bcfc4f49d56417: colère
5a380af6e3bcfc4f49d56419: amour
5a380af6e3bcfc4f49d5641b: peur
5a380af7e3bcfc4f49d5641d: amour
5a380af7e3bcfc4f49d5641f: amour
5a380af7e3bcfc4f49d56423: colère
5a380af7e3bcfc4f49d56425: amour
5a380af7e3bcfc4f49d56427: amour
5a380af8e3bcfc4f49d56429: joie
5a380af8e3bcfc4f49d5642b: joie


...

5a384197e3bcfc4f49d782af: amour
5a384198e3bcfc4f49d782b1: amour
5a384198e3bcfc4f49d782b3: peur
5a384198e3bcfc4f49d782b5: espoir
5a384198e3bcfc4f49d782b7: espoir
5a384199e3bcfc4f49d782b9: amour
5a384199e3bcfc4f49d782bb: colère
5a384199e3bcfc4f49d782c1: espoir
5a384199e3bcfc4f49d782c3: amour
5a384199e3bcfc4f49d782c5: amour
5a384199e3bcfc4f49d782c7: amour
5a38419ae3bcfc4f49d782cd: amour
5a3841d1e3bcfc4f49d78585: amour
5a3841d1e3bcfc4f49d7858d: amour
5a3841d1e3bcfc4f49d7858f: amour
5a3841d2e3bcfc4f49d78591: amour
5a3841d2e3bcfc4f49d78593: colère
5a3841d2e3bcfc4f49d78595: colère
5a3841d2e3bcfc4f49d78597: amour
5a3841d2e3bcfc4f49d78599: luxure
5a3841d3e3bcfc4f49d7859b: espoir
5a3841d3e3bcfc4f49d7859f: amour
5a3841d3e3bcfc4f49d785a1: amour
5a3841d3e3bcfc4f49d785a3: peur
5a3841d3e3bcfc4f49d785a5: amour
5a3841d4e3bcfc4f49d785a7: amour
5a3841d4e3bcfc4f49d785a9: amour
5a3841d4e3bcfc4f49d785ab: colère
5a3841d4e3bcfc4f49d785ad: amour
5a3841d4e3bcfc4f49d785af: amour
5a3841d5e3bcfc4f49d785b1: peur
5a

5a38463ae3bcfc4f49d7b0b1: espoir
5a38463ae3bcfc4f49d7b0b3: espoir
5a38463be3bcfc4f49d7b0b5: peur
5a38463be3bcfc4f49d7b0b7: joie
5a38463be3bcfc4f49d7b0b9: espoir
5a38463be3bcfc4f49d7b0bd: amour
5a38463ce3bcfc4f49d7b0bf: espoir
5a384658e3bcfc4f49d7b26e: amour
5a384658e3bcfc4f49d7b270: joie
5a384658e3bcfc4f49d7b272: espoir
5a384658e3bcfc4f49d7b274: joie
5a384658e3bcfc4f49d7b276: joie
5a384658e3bcfc4f49d7b278: amour
5a384658e3bcfc4f49d7b27a: amour
5a384658e3bcfc4f49d7b27c: luxure
5a384659e3bcfc4f49d7b27e: amour
5a384659e3bcfc4f49d7b280: espoir
5a384659e3bcfc4f49d7b282: tristesse
5a384659e3bcfc4f49d7b284: espoir
5a384659e3bcfc4f49d7b286: luxure
5a384659e3bcfc4f49d7b288: amour
5a38465ae3bcfc4f49d7b28a: colère
5a38465ae3bcfc4f49d7b28c: luxure
5a38465ae3bcfc4f49d7b28e: espoir
5a38465ae3bcfc4f49d7b292: luxure
5a38465ae3bcfc4f49d7b294: amour
5a38465ae3bcfc4f49d7b298: peur
5a38465ae3bcfc4f49d7b29a: espoir
5a38465be3bcfc4f49d7b29e: colère
5a38465be3bcfc4f49d7b2a0: espoir
5a38465be3bcfc4f49d7b2a2: 

5a384baae3bcfc4f49d7e935: amour
5a384baae3bcfc4f49d7e937: luxure
5a384baae3bcfc4f49d7e939: amour
5a384baae3bcfc4f49d7e93b: amour
5a384baae3bcfc4f49d7e93d: colère
5a384baae3bcfc4f49d7e93f: espoir
5a384baae3bcfc4f49d7e941: amour
5a384baae3bcfc4f49d7e945: amour
5a384babe3bcfc4f49d7e947: amour
5a384babe3bcfc4f49d7e949: espoir
5a384babe3bcfc4f49d7e94b: espoir
5a384babe3bcfc4f49d7e94d: espoir
5a384babe3bcfc4f49d7e94f: amour
5a384babe3bcfc4f49d7e951: espoir
5a384babe3bcfc4f49d7e953: tristesse
5a384bace3bcfc4f49d7e955: amour
5a384bace3bcfc4f49d7e959: espoir
5a384bace3bcfc4f49d7e95b: amour
5a384bace3bcfc4f49d7e95d: amour
5a384bace3bcfc4f49d7e95f: amour
5a384bace3bcfc4f49d7e961: amour
5a384bace3bcfc4f49d7e963: espoir
5a384bace3bcfc4f49d7e965: espoir
5a384bade3bcfc4f49d7e967: espoir
5a384bade3bcfc4f49d7e969: espoir
5a384bade3bcfc4f49d7e96b: amour
5a384bade3bcfc4f49d7e96d: amour
5a384bade3bcfc4f49d7e96f: luxure
5a384bade3bcfc4f49d7e973: amour
5a384bade3bcfc4f49d7e975: espoir
5a384bade3bcfc4f49d7e9

5a3851b2e3bcfc4f49d82d47: espoir
5a3851b2e3bcfc4f49d82d49: joie
5a3851b2e3bcfc4f49d82d4b: amour
5a3851b2e3bcfc4f49d82d4d: luxure
5a3851b3e3bcfc4f49d82d4f: amour
5a3851b3e3bcfc4f49d82d51: amour
5a3851b3e3bcfc4f49d82d53: amour
5a3851b3e3bcfc4f49d82d55: amour
5a3851b3e3bcfc4f49d82d57: joie
5a3851b3e3bcfc4f49d82d59: amour
5a3851b3e3bcfc4f49d82d5b: amour
5a3851b4e3bcfc4f49d82d5d: amour
5a3851b4e3bcfc4f49d82d5f: amour
5a3851b4e3bcfc4f49d82d61: espoir
5a3851b4e3bcfc4f49d82d63: amour
5a3851b4e3bcfc4f49d82d65: amour
5a3851b4e3bcfc4f49d82d67: peur
5a3851b5e3bcfc4f49d82d69: amour
5a3851b5e3bcfc4f49d82d6b: espoir
5a3851b5e3bcfc4f49d82d6d: luxure
5a3851b5e3bcfc4f49d82d6f: amour
5a3851b6e3bcfc4f49d82d71: amour
5a3851b6e3bcfc4f49d82d73: luxure
5a3851b6e3bcfc4f49d82d75: luxure
5a3851b6e3bcfc4f49d82d77: peur
5a3851b6e3bcfc4f49d82d7b: amour
5a3851b6e3bcfc4f49d82d7d: peur
5a3851b6e3bcfc4f49d82d7f: espoir
5a3851b7e3bcfc4f49d82d81: espoir
5a3851b7e3bcfc4f49d82d83: espoir
5a3851b7e3bcfc4f49d82d85: colère
5a

5a3852e8e3bcfc4f49d83dd0: espoir
5a3852e8e3bcfc4f49d83dd2: luxure
5a3852e8e3bcfc4f49d83dd4: peur
5a3852e8e3bcfc4f49d83dd6: espoir
5a3852e9e3bcfc4f49d83dd8: espoir
5a3852e9e3bcfc4f49d83dda: colère
5a3852e9e3bcfc4f49d83ddc: amour
5a3852e9e3bcfc4f49d83de0: amour
5a3852e9e3bcfc4f49d83de2: amour
5a3852eae3bcfc4f49d83de4: amour
5a3852eae3bcfc4f49d83de6: amour
5a3852eae3bcfc4f49d83de8: espoir
5a3852eae3bcfc4f49d83dea: espoir
5a3852ebe3bcfc4f49d83dec: amour
5a3852ebe3bcfc4f49d83dee: amour
5a3852ebe3bcfc4f49d83df0: amour
5a3852ebe3bcfc4f49d83df2: peur
5a3852ebe3bcfc4f49d83df4: tristesse
5a3852ebe3bcfc4f49d83df6: espoir
5a3852ebe3bcfc4f49d83dfa: colère
5a3852ece3bcfc4f49d83dfc: espoir
5a3852ece3bcfc4f49d83dfe: luxure
5a3852ece3bcfc4f49d83e00: peur
5a3852ece3bcfc4f49d83e02: amour
5a3852ece3bcfc4f49d83e04: colère
5a3852ece3bcfc4f49d83e06: luxure
5a3852ece3bcfc4f49d83e08: joie
5a3852ede3bcfc4f49d83e0a: amour
5a3852ede3bcfc4f49d83e0c: amour
5a3852ede3bcfc4f49d83e0e: joie
5a3852ede3bcfc4f49d83e12: am

In [32]:
#Code test, prédit toutes les musiques dans list_low_en
#Output: Dictionnaire => id : sentiment prédit
dico_test = {}
for i in range(0,len(list_low_en)):
    music_pred_en=list_low_en[i][2]
    senti_en=predict_sentiment(music_pred_en, dict_sentiment_en_stem)
    dico_test[list_low_en[i][0]]=(max(senti_en.items(), key=operator.itemgetter(1))[0])
    
#Lit le dico et l'enregistre dans un csv, utilisé pour l'annotation
with open("labeled.csv", 'w') as csv_file:
    fieldnames = ['id', 'sentiment']
    writer = csv.DictWriter(csv_file, fieldnames=fieldnames, delimiter=",")

    writer.writeheader()
    for key in dico_test:
        writer.writerow({'id': key, 'sentiment': dico_test[key]})

KeyboardInterrupt: 

In [242]:
#Lit le csv et l'enregistre dans un dico
dico_test2 = {}
with open('labeled.csv') as csv_file:
    reader = csv.DictReader(csv_file)
    for row in reader:
        data=str(row).split(",")
        dico_test2[str(data[1]).split("\'")[1]]=str(data[3]).split("\'")[1]
print(dico_test2)

{'5a37f60de3bcfc4f49d4996b': 'amour', '5a37f60de3bcfc4f49d4996d': 'espoir', '5a37f60de3bcfc4f49d4996f': 'espoir', '5a37f60de3bcfc4f49d49971': 'espoir', '5a37f60de3bcfc4f49d49973': 'amour', '5a37f60de3bcfc4f49d49977': 'espoir', '5a37f60de3bcfc4f49d49979': 'espoir', '5a37f60de3bcfc4f49d4997b': 'espoir', '5a37f60de3bcfc4f49d49980': 'colère', '5a37f60ee3bcfc4f49d4998d': 'luxure', '5a37f60ee3bcfc4f49d4998f': 'colère', '5a37f60fe3bcfc4f49d49991': 'espoir', '5a37f60fe3bcfc4f49d49993': 'espoir', '5a37f60fe3bcfc4f49d49995': 'colère', '5a37f60fe3bcfc4f49d49997': 'colère', '5a37f60fe3bcfc4f49d49999': 'espoir', '5a37f60fe3bcfc4f49d4999b': 'espoir', '5a37f60fe3bcfc4f49d4999e': 'espoir', '5a37f60fe3bcfc4f49d499a0': 'colère', '5a37f610e3bcfc4f49d499a3': 'espoir', '5a37f610e3bcfc4f49d499a5': 'colère', '5a37f610e3bcfc4f49d499a7': 'espoir', '5a37f610e3bcfc4f49d499a9': 'espoir', '5a37f610e3bcfc4f49d499ab': 'amour', '5a37f610e3bcfc4f49d499ad': 'colère', '5a37f610e3bcfc4f49d499af': 'espoir', '5a37f611e3bcf